In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
import pandas as pd
import matplotlib.pyplot as plt
from torch.utils.data import Dataset, DataLoader
from sklearn.preprocessing import MinMaxScaler

In [ ]:


# Load dataset from uploaded CSV file (ensure it's a single column with 'Close' values)
file_path = "Stock_prices.csv"
df = pd.read_csv(file_path)

# Use only 'Close' prices for prediction
df = df[['Close']].dropna()

# Normalize data
scaler = MinMaxScaler(feature_range=(0, 1))
df['Close'] = scaler.fit_transform(df[['Close']])


In [ ]:
# Define dataset class
class StockDataset(Dataset):
    def __init__(self, data, lookback=60):
        self.data = torch.tensor(data, dtype=torch.float32)  # Convert data to PyTorch tensor
        self.lookback = lookback
        self.X, self.y = self.create_sequences()

    def create_sequences(self):
        X, y = [], []
        for i in range(len(self.data) - self.lookback):
            X.append(self.data[i : i + self.lookback])
            y.append(self.data[i + self.lookback])
        
        # Stack list elements into a single tensor
        return torch.stack(X), torch.stack(y)

    def __len__(self):
        return len(self.X)

    def __getitem__(self, idx):
        return self.X[idx], self.y[idx]

In [ ]:

# Split data (No random shuffling, maintaining time-series order)
split_index = int(len(df) * 0.8)
train_data, test_data = df[:split_index].values, df[split_index:].values

# Create datasets and dataloaders
lookback = 60
train_dataset = StockDataset(train_data, lookback)
test_dataset = StockDataset(test_data, lookback)

train_loader = DataLoader(train_dataset, batch_size=32, shuffle=False)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)


In [ ]:
# Define neural network model
class StockPredictor(nn.Module):
    def __init__(self):
        super(StockPredictor, self).__init__()
        self.lstm = nn.LSTM(input_size=1, hidden_size=50, num_layers=2, batch_first=True)
        self.fc = nn.Linear(50, 1)

    def forward(self, x):
        lstm_out, _ = self.lstm(x)
        return self.fc(lstm_out[:, -1, :])


In [ ]:

# Initialize model, loss, optimizer
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = StockPredictor().to(device)
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

In [ ]:
# Training loop
def train_model(model, train_loader, criterion, optimizer, epochs=20):
    model.train()
    for epoch in range(epochs):
        epoch_loss = 0.0
        for inputs, targets in train_loader:
            inputs, targets = inputs.to(device), targets.to(device)
            targets = targets.squeeze(-1)  # Reshape for LSTM
            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs, targets.unsqueeze(1))
            loss.backward()
            optimizer.step()
            epoch_loss += loss.item()
        print(f"Epoch {epoch+1}/{epochs}, Loss: {epoch_loss / len(train_loader):.6f}")

# Train the model
train_model(model, train_loader, criterion, optimizer)

In [ ]:
# Function to make predictions
def make_predictions(model, dataloader, dataset, scaler):
    model.eval()
    predictions, actuals = [], []
    
    with torch.no_grad():
        for inputs, targets in dataloader:
            inputs = inputs.to(device)
            output = model(inputs).cpu()
            
            predictions.append(output)
            actuals.append(targets.cpu())

    # Convert lists of tensors into single tensors and reshape them
    predictions = torch.cat(predictions, dim=0).reshape(-1, 1)
    actuals = torch.cat(actuals, dim=0).reshape(-1, 1)

    # Perform inverse scaling in PyTorch (assuming `scaler` is a MinMaxScaler)
    predictions = torch.tensor(scaler.inverse_transform(predictions.numpy()), dtype=torch.float32)
    actuals = torch.tensor(scaler.inverse_transform(actuals.numpy()), dtype=torch.float32)

    return predictions, actuals

In [ ]:
# Get predictions
train_predictions, train_actuals = make_predictions(model, train_loader, train_dataset, scaler)
test_predictions, test_actuals = make_predictions(model, test_loader, test_dataset, scaler)

# Get corresponding dates
train_dates = df.index[:split_index][lookback:]
test_dates = df.index[split_index:][lookback:]

In [ ]:

# Plot results
plt.figure(figsize=(12, 6))
plt.plot(train_dates, train_actuals, label="Train Actual", color="blue")
plt.plot(train_dates, train_predictions, label="Train Predicted", color="cyan", linestyle="dashed")
plt.plot(test_dates, test_actuals, label="Test Actual", color="green")
plt.plot(test_dates, test_predictions, label="Test Predicted", color="red", linestyle="dashed")

# Formatting
plt.xlabel("Date")
plt.ylabel("Stock Price")
plt.title("Stock Price Prediction")
plt.legend()
plt.xticks(rotation=45)
plt.grid()

# Show plot
plt.show()